# Matrix Generation

In [1]:
import sys
sys.path.append("../")
from Recipe import Recipe, Ingredient, RecipeGraph

import settings
import db.db_settings as db_settings
from db.database_connection import DatabaseConnection

import random

import itertools

import numpy as np

In [2]:
DatabaseConnection(db_settings.db_host,
                   db_settings.db_port,
                   db_settings.db_user,
                   db_settings.db_pw,
                   db_settings.db_db,
                   db_settings.db_charset)

In [3]:
%time ids = DatabaseConnection.global_single_query("select id from recipes")

CPU times: user 8.71 s, sys: 942 ms, total: 9.66 s
Wall time: 9.77 s


In [4]:
import AdjacencyMatrix

* create Adjacency Matrix

In [6]:
def add_entries_from_rec_state(rec_state, m_act, m_mix, m_base_act, m_base_mix):
    mix_m, mix_label = rec_state.get_mixing_matrix()
    act_m, act_a, act_i = rec_state.get_action_matrix()

    # create list of tuples: [action, ingredient]
    seen_actions = np.array(list(itertools.product(act_a,act_i))).reshape((len(act_a), len(act_i), 2))

    # create list of tuples [ingredient, ingredient]
    seen_mixes = np.array(list(itertools.product(mix_label,mix_label))).reshape((len(mix_label), len(mix_label), 2))

    seen_actions = seen_actions[act_m == 1]
    seen_mixes = seen_mixes[mix_m == 1]

    seen_actions = set([tuple(x) for x in seen_actions.tolist()])
    seen_mixes = set([tuple(x) for x in seen_mixes.tolist()])
    
    seen_base_actions = set()
    seen_base_mixes = set()
    
    for act, ing in seen_actions:
        m_act.add_entry(act, ing.to_json(), 1)
        if (act, ing._base_ingredient) not in seen_base_actions:
            seen_base_actions.add((act, ing._base_ingredient))
            m_base_act.add_entry(act, ing._base_ingredient, 1)
    
    for x,y in seen_mixes:
        xj = x.to_json()
        yj = y.to_json()
        if xj < yj:
            m_mix.add_entry(xj,yj,1)
            if (x._base_ingredient, y._base_ingredient) not in seen_base_mixes:
                seen_base_mixes.add((x._base_ingredient, y._base_ingredient))
                m_base_mix.add_entry(x._base_ingredient, y._base_ingredient, 1)
    

In [7]:
m_act = AdjacencyMatrix.adj_matrix()
m_mix = AdjacencyMatrix.adj_matrix(True)
m_base_act = AdjacencyMatrix.adj_matrix()
m_base_mix = AdjacencyMatrix.adj_matrix(True)

In [8]:
%%time
for i in range(10000):
    id = random.choice(ids)['id']
    rec = Recipe(id)
    #rec.display_recipe()
    ing = rec.extract_ingredients()
    if len(ing) == 0:
        print(f"warning: recipe {id} has no ingredient! skipping it")
        continue
    rec.apply_instructions(debug=False)
    add_entries_from_rec_state(rec._recipe_state, m_act, m_mix, m_base_act, m_base_mix)

CPU times: user 13min 35s, sys: 3.52 s, total: 13min 39s
Wall time: 13min 50s


In [10]:
import pickle

In [11]:
pickle.dump(m_act, file=open("m_act.pickle", 'wb'))
pickle.dump(m_mix, file=open("m_mix.pickle", 'wb'))
pickle.dump(m_base_act, file=open("m_base_act.pickle", 'wb'))
pickle.dump(m_base_mix, file=open("m_base_mix.pickle", 'wb'))

In [12]:
c_mix = m_mix.get_csr()
c_act = m_act.get_csr()
c_base_mix = m_base_mix.get_csr()
c_base_act = m_base_act.get_csr()

In [13]:
print(c_act.shape, c_mix.shape)
print(len(c_act.nonzero()[0]),len(c_mix.nonzero()[0]))
print(c_base_act.shape, c_base_mix.shape)
print(len(c_base_act.nonzero()[0]),len(c_base_mix.nonzero()[0]))

(65, 64699) (71548, 71548)
113994 537369
(65, 4738) (5850, 5850)
30820 122390


In [16]:
print(c_act.shape, c_mix.shape)
print(len(c_act.nonzero()[0]),len(c_mix.nonzero()[0]))

(64, 63787) (70933, 70933)
112841 524285


In [18]:
np.sum(c_act.toarray() > 1)

17560

array([[1, 1, 0, ..., 0, 0, 0],
       [0, 0, 1, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

* values after 100:
```
(53, 1498) (1620, 1620)
1982 6489
```

* after 1000:
```
(60, 9855) (10946, 10946)
15446 59943
```

* after 10000:
```
(65, 65235) (72448, 72448)
114808 546217
```